This notebook generates maps for the UI mockup answering the following 3 questions:
* What samples are new landfill or DOD sites?
* What surface water bodies are new landfill or DOD sites?
* What surface water bodies are downstream from landfill or DOD sites?

# Setup


In [1]:
%%capture
!pip install mapclassify --upgrade --quiet
!pip install SPARQLWrapper --upgrade --quiet
!pip install rdflib

In [2]:
#from branca.element import Figure                                  # For controlling the size of the final map
import folium                                                      # For map layer control
import geopandas as gpd                                            # For geospatial dataframes
import pandas as pd                                                # For dataframes
from shapely import wkt                                            # For working with WKT coordinates in a GeoDataFrame
from SPARQLWrapper import SPARQLWrapper2, JSON, GET, POST, DIGEST   # For querying SPARQL endpoints
import rdflib                                                      # For working with URIs

In [3]:
endpointGET = 'https://gdb.acg.maine.edu:7201/repositories/PFAS'

sparqlGET = SPARQLWrapper2(endpointGET)
sparqlGET.setHTTPAuth(DIGEST)
sparqlGET.setCredentials('sawgraph-endpoint', 'skailab')
sparqlGET.setMethod(GET)
sparqlGET.setReturnFormat(JSON)

In [4]:
def convertToDataframe(results):
  d = []
  for x in results.bindings:
        row = {}
        for k in x:
            v = x[k]
            vv = rdflib.term.Literal(v.value, datatype=v.datatype).toPython()  # type: ignore[no-untyped-call]
            row[k] = vv
        d.append(row)
  df = pd.DataFrame(d)
  return df

# Q1 - What samples in Maine are near landfill or DOD sites?


## Queries

In [5]:
%%time

q1='''
PREFIX dcterms: <http://purl.org/dc/terms/>
PREFIX qudt: <http://qudt.org/schema/qudt/>
PREFIX skos: <http://www.w3.org/2004/02/skos/core#>
PREFIX geo: <http://www.opengis.net/ont/geosparql#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX naics: <http://w3id.org/fio/v1/naics#>
PREFIX spatial: <http://purl.org/spatialai/spatial/spatial-full#>
PREFIX kwgr: <http://stko-kwg.geog.ucsb.edu/lod/resource/>
PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX coso: <http://w3id.org/coso/v1/contaminoso#>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX fio: <http://w3id.org/fio/v1/fio#>

PREFIX owl: <http://www.w3.org/2002/07/owl#>
select DISTINCT ?samplePoint ?spWKT ?sample (GROUP_CONCAT(DISTINCT ?sampleId; separator="; ") as ?samples) (COUNT(DISTINCT ?subVal) as ?resultCount) (MAX(?result) as ?Max) ?unit (GROUP_CONCAT(DISTINCT ?subVal; separator=" <br> ") as ?results)
where {
        SERVICE <repository:FIO>{
        #find facilities
        ?s2neighbor kwg-ont:sfContains ?facility.
        ?facility fio:ofIndustry ?industry;
        		#geo:hasGeometry/geo:asWKT ?facWKT;
        		#rdfs:label ?facilityName.
        #?industry rdfs:label ?industryName.
        VALUES ?industry {naics:NAICS-562212 naics:NAICS-928110}.
    }
            SERVICE <repository:Spatial>{
        #determine near distance
        ?s2 kwg-ont:sfTouches|owl:sameAs ?s2neighbor.
        ?s2neighbor rdf:type kwg-ont:S2Cell_Level13.
    }
    #find samples
    ?samplePoint kwg-ont:sfWithin ?s2;
    	rdf:type coso:SamplePoint;
    	geo:hasGeometry/geo:asWKT ?spWKT.
    ?s2 rdf:type kwg-ont:S2Cell_Level13.
    ?sample coso:fromSamplePoint ?samplePoint;
    	dcterms:identifier ?sampleId;
    	coso:sampleOfMaterialType/rdfs:label ?type.
    ?observation rdf:type coso:ContaminantObservation;
    	coso:observedAtSamplePoint ?samplePoint;
    	coso:ofSubstance/ skos:altLabel ?substance;
    	coso:hasResult/coso:measurementValue ?result;
    	coso:hasResult/coso:measurementUnit/qudt:symbol ?unit.
    BIND((CONCAT(?substance, ": ", str(?result) , " ", ?unit) ) as ?subVal)

    } GROUP BY ?samplePoint ?spWKT ?sample ?unit
'''
#What SAMPLES are NEAR to LANDFILLS or DOD facilities?
q2 = '''
PREFIX geo: <http://www.opengis.net/ont/geosparql#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX naics: <http://w3id.org/fio/v1/naics#>
PREFIX spatial: <http://purl.org/spatialai/spatial/spatial-full#>
PREFIX kwgr: <http://stko-kwg.geog.ucsb.edu/lod/resource/>
PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX coso: <http://w3id.org/coso/v1/contaminoso#>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX fio: <http://w3id.org/fio/v1/fio#>

#Where are landfills or dod facilities

select DISTINCT ?facility ?facWKT ?facilityName ?industry ?industryName where {
    #SERVICE <repository:Spatial>{
    #    #determine near distance
    #    ?s2 kwg-ont:sfTouches|owl:sameAs ?s2neighbor.
    #    ?s2neighbor rdf:type kwg-ont:S2Cell_Level13.
    #}
    SERVICE <repository:FIO>{
        #find facilities
        #?s2neighbor kwg-ont:sfContains ?facility.
        ?facility fio:ofIndustry ?industry;
        		geo:hasGeometry/geo:asWKT ?facWKT;
        		rdfs:label ?facilityName.
        ?industry rdfs:label ?industryName.
        VALUES ?industry {naics:NAICS-562212 naics:NAICS-928110}.
    }

}
'''

CPU times: user 5 µs, sys: 1 µs, total: 6 µs
Wall time: 9.78 µs


In [6]:
%%time
sparqlGET.setQuery(q1)
samplepoint_result = sparqlGET.query()
samplepoints = convertToDataframe(samplepoint_result)


CPU times: user 186 ms, sys: 48 ms, total: 235 ms
Wall time: 22.3 s


In [7]:
samplepoints

samplePoint  \
0     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
1     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
3     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
4     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
...                                                 ...   
2244  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2245  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2246  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2247  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2248  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   

                               spWKT  \
0     POINT (-70.3774068 43.6478468)   
1     POINT (-70.3774068 43.6478468)   
2     POINT (-70.3774068 43.6478468)   
3     POINT (-70.3774068 43.6478468)   
4     POINT (-70.3790242 43.6456832)   
...                              ...   
2244  POINT (-70.7501762 43.1199148)   
2245   POINT (-70.7505721 43.119733)   
2246  POINT (-70.7517553 43.1211201)   
2247  POINT (-70.7478058 43.1241882)   
2248  POINT (-70.7433161 43.1186618)   

                                                 sample        samples  \
0     http://w3id.org/sawgraph/v1/me-egad-data#sampl...           DW-2   
1     http://w3id.org/sawgraph/v1/me-egad-data#sampl...          DW 10   
2     http://w3id.org/sawgraph/v1/me-egad-data#sampl...       DW-2D PT   
3     http://w3id.org/sawgraph/v1/me-egad-data#sampl...           DW-1   
4     http://w3id.org/sawgraph/v1/me-egad-data#sampl...           DW-1   
...                                                 ...            ...   
2244  http://w3id.org/sawgraph/v1/me-egad-data#sampl...          B101B   
2245  http://w3id.org/sawgraph/v1/me-egad-data#sampl...           B110   
2246  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   KITTERY PW-1   
2247  http://w3id.org/sawgraph/v1/me-egad-data#sampl...  67 WILSON RD.   
2248  http://w3id.org/sawgraph/v1/me-egad-data#sampl...    4 PETTIGREW   

      resultCount    Max  unit  \
0              53   50.2  ng/L   
1              53   50.2  ng/L   
2              53   50.2  ng/L   
3              53   50.2  ng/L   
4              16  85.92  ng/L   
...           ...    ...   ...   
2244           14   97.0  ng/L   
2245           16  538.0  ng/L   
2246           20  317.0  ng/L   
2247           12   4.88  ng/L   
2248            7   3.46  ng/L   

                                                results  
0     PFOS_A: 6.29 ng/L <br> PFOS_A_L + PFOS_A_BR: 6...  
1     PFOS_A: 6.29 ng/L <br> PFOS_A_L + PFOS_A_BR: 6...  
2     PFOS_A: 6.29 ng/L <br> PFOS_A_L + PFOS_A_BR: 6...  
3     PFOS_A: 6.29 ng/L <br> PFOS_A_L + PFOS_A_BR: 6...  
4     PFOS_A: 36.8 ng/L <br> PFOS_A_L + PFOS_A_BR: 3...  
...                                                 ...  
2244  PFOS_A: 25.4 ng/L <br> PFOS_A_L + PFOS_A_BR: 2...  
2245  PFOS_A: 43.6 ng/L <br> PFOS_A_L + PFOS_A_BR: 4...  
2246  PFOS_A: 79.6 ng/L <br> PFOS_A_L + PFOS_A_BR: 7...  
2247  PFOS_A: 2.63 ng/L <br> PFOS_A_L + PFOS_A_BR: 2...  
2248  PFPEA_A: 3.46 ng/L <br> PFHXA_A: 3.16 ng/L <br...  

[2249 rows x 8 columns]

In [8]:
# truncate results that are very long
samplepoints['results'] = samplepoints['results'].apply(lambda x: "<br> ".join(x.split('<br>')[0:20])+"<br> ... " if len(x.split('<br>')) > 16 else x)

In [9]:
samplepoints

samplePoint  \
0     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
1     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
3     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
4     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
...                                                 ...   
2244  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2245  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2246  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2247  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2248  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   

                               spWKT  \
0     POINT (-70.3774068 43.6478468)   
1     POINT (-70.3774068 43.6478468)   
2     POINT (-70.3774068 43.6478468)   
3     POINT (-70.3774068 43.6478468)   
4     POINT (-70.3790242 43.6456832)   
...                              ...   
2244  POINT (-70.7501762 43.1199148)   
2245   POINT (-70.7505721 43.119733)   
2246  POINT (-70.7517553 43.1211201)   
2247  POINT (-70.7478058 43.1241882)   
2248  POINT (-70.7433161 43.1186618)   

                                                 sample        samples  \
0     http://w3id.org/sawgraph/v1/me-egad-data#sampl...           DW-2   
1     http://w3id.org/sawgraph/v1/me-egad-data#sampl...          DW 10   
2     http://w3id.org/sawgraph/v1/me-egad-data#sampl...       DW-2D PT   
3     http://w3id.org/sawgraph/v1/me-egad-data#sampl...           DW-1   
4     http://w3id.org/sawgraph/v1/me-egad-data#sampl...           DW-1   
...                                                 ...            ...   
2244  http://w3id.org/sawgraph/v1/me-egad-data#sampl...          B101B   
2245  http://w3id.org/sawgraph/v1/me-egad-data#sampl...           B110   
2246  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   KITTERY PW-1   
2247  http://w3id.org/sawgraph/v1/me-egad-data#sampl...  67 WILSON RD.   
2248  http://w3id.org/sawgraph/v1/me-egad-data#sampl...    4 PETTIGREW   

      resultCount    Max  unit  \
0              53   50.2  ng/L   
1              53   50.2  ng/L   
2              53   50.2  ng/L   
3              53   50.2  ng/L   
4              16  85.92  ng/L   
...           ...    ...   ...   
2244           14   97.0  ng/L   
2245           16  538.0  ng/L   
2246           20  317.0  ng/L   
2247           12   4.88  ng/L   
2248            7   3.46  ng/L   

                                                results  
0     PFOS_A: 6.29 ng/L <br>  PFOS_A_L + PFOS_A_BR: ...  
1     PFOS_A: 6.29 ng/L <br>  PFOS_A_L + PFOS_A_BR: ...  
2     PFOS_A: 6.29 ng/L <br>  PFOS_A_L + PFOS_A_BR: ...  
3     PFOS_A: 6.29 ng/L <br>  PFOS_A_L + PFOS_A_BR: ...  
4     PFOS_A: 36.8 ng/L <br> PFOS_A_L + PFOS_A_BR: 3...  
...                                                 ...  
2244  PFOS_A: 25.4 ng/L <br> PFOS_A_L + PFOS_A_BR: 2...  
2245  PFOS_A: 43.6 ng/L <br> PFOS_A_L + PFOS_A_BR: 4...  
2246  PFOS_A: 79.6 ng/L <br>  PFOS_A_L + PFOS_A_BR: ...  
2247  PFOS_A: 2.63 ng/L <br> PFOS_A_L + PFOS_A_BR: 2...  
2248  PFPEA_A: 3.46 ng/L <br> PFHXA_A: 3.16 ng/L <br...  

[2249 rows x 8 columns]

In [10]:
%%time
sparqlGET.setQuery(q2)
facility_result = sparqlGET.query()
facilities = convertToDataframe(facility_result)
#print(facilities.info())
facilities

CPU times: user 53.4 ms, sys: 6.47 ms, total: 59.8 ms
Wall time: 1min 54s


facility  \
0     http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
1     http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
2     http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
3     http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
4     http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
...                                                 ...   
1279  http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
1280  http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
1281  http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
1282  http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
1283  http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   

                            facWKT  \
0     POINT (-70.260749 44.067531)   
1     POINT (-70.359644 43.645986)   
2     POINT (-69.847255 44.712556)   
3       POINT (-70.18693 44.04928)   
4     POINT (-68.825833 44.738333)   
...                            ...   
1279  POINT (-84.476705 39.457957)   
1280  POINT (-82.965169 39.356438)   
1281    POINT (-80.97715 40.25527)   
1282   POINT (-84.053745 39.81373)   
1283    POINT (-83.78647 41.59144)   

                                           facilityName  \
0                MID MAINE WASTE - TO - ENERGY FACILITY   
1                                     ECOMAINE LANDFILL   
2     WASTE MANAGEMENT DISPOSALSERVICES OF MAINE, IN...   
3             LEWISTON SOLID WASTE & RECYCLING FACILITY   
4                    PENOBSCOT ENERGY RECOVERY FACILITY   
...                                                 ...   
1279                88TH REGIONAL SUPPORT COMMAND USARC   
1280        US ARMY NATIONAL GUARD RANGE - CAMP SHERMAN   
1281  88TH REGIONAL SUPPORT COMMAND SSG GEORGE J CON...   
1282             U.S. AIR FORCE WRIGHT-PATTERSON AFB OH   
1283         180TH FIGHTER WING/OHIO AIR NATIONAL GUARD   

                                       industry           industryName  
0     http://w3id.org/fio/v1/naics#NAICS-562212  Solid Waste Landfill   
1     http://w3id.org/fio/v1/naics#NAICS-562212  Solid Waste Landfill   
2     http://w3id.org/fio/v1/naics#NAICS-562212  Solid Waste Landfill   
3     http://w3id.org/fio/v1/naics#NAICS-562212  Solid Waste Landfill   
4     http://w3id.org/fio/v1/naics#NAICS-562212  Solid Waste Landfill   
...                                         ...                    ...  
1279  http://w3id.org/fio/v1/naics#NAICS-928110     National Security   
1280  http://w3id.org/fio/v1/naics#NAICS-928110     National Security   
1281  http://w3id.org/fio/v1/naics#NAICS-928110     National Security   
1282  http://w3id.org/fio/v1/naics#NAICS-928110     National Security   
1283  http://w3id.org/fio/v1/naics#NAICS-928110     National Security   

[1284 rows x 5 columns]

## Prep data for mapping

In [11]:
samplepoints['spWKT'] = samplepoints['spWKT'].apply(wkt.loads)
samplepoints = gpd.GeoDataFrame(samplepoints, geometry='spWKT')


In [12]:
facilities['facWKT'] = facilities['facWKT'].apply(wkt.loads)
facilities = gpd.GeoDataFrame(facilities, geometry='facWKT')

In [13]:
samplepoints.set_crs(epsg=4326, inplace=True, allow_override=True)


samplePoint  \
0     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
1     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
3     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
4     http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
...                                                 ...   
2244  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2245  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2246  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2247  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2248  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   

                           spWKT  \
0     POINT (-70.37741 43.64785)   
1     POINT (-70.37741 43.64785)   
2     POINT (-70.37741 43.64785)   
3     POINT (-70.37741 43.64785)   
4     POINT (-70.37902 43.64568)   
...                          ...   
2244  POINT (-70.75018 43.11991)   
2245  POINT (-70.75057 43.11973)   
2246  POINT (-70.75176 43.12112)   
2247  POINT (-70.74781 43.12419)   
2248  POINT (-70.74332 43.11866)   

                                                 sample        samples  \
0     http://w3id.org/sawgraph/v1/me-egad-data#sampl...           DW-2   
1     http://w3id.org/sawgraph/v1/me-egad-data#sampl...          DW 10   
2     http://w3id.org/sawgraph/v1/me-egad-data#sampl...       DW-2D PT   
3     http://w3id.org/sawgraph/v1/me-egad-data#sampl...           DW-1   
4     http://w3id.org/sawgraph/v1/me-egad-data#sampl...           DW-1   
...                                                 ...            ...   
2244  http://w3id.org/sawgraph/v1/me-egad-data#sampl...          B101B   
2245  http://w3id.org/sawgraph/v1/me-egad-data#sampl...           B110   
2246  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   KITTERY PW-1   
2247  http://w3id.org/sawgraph/v1/me-egad-data#sampl...  67 WILSON RD.   
2248  http://w3id.org/sawgraph/v1/me-egad-data#sampl...    4 PETTIGREW   

      resultCount    Max  unit  \
0              53   50.2  ng/L   
1              53   50.2  ng/L   
2              53   50.2  ng/L   
3              53   50.2  ng/L   
4              16  85.92  ng/L   
...           ...    ...   ...   
2244           14   97.0  ng/L   
2245           16  538.0  ng/L   
2246           20  317.0  ng/L   
2247           12   4.88  ng/L   
2248            7   3.46  ng/L   

                                                results  
0     PFOS_A: 6.29 ng/L <br>  PFOS_A_L + PFOS_A_BR: ...  
1     PFOS_A: 6.29 ng/L <br>  PFOS_A_L + PFOS_A_BR: ...  
2     PFOS_A: 6.29 ng/L <br>  PFOS_A_L + PFOS_A_BR: ...  
3     PFOS_A: 6.29 ng/L <br>  PFOS_A_L + PFOS_A_BR: ...  
4     PFOS_A: 36.8 ng/L <br> PFOS_A_L + PFOS_A_BR: 3...  
...                                                 ...  
2244  PFOS_A: 25.4 ng/L <br> PFOS_A_L + PFOS_A_BR: 2...  
2245  PFOS_A: 43.6 ng/L <br> PFOS_A_L + PFOS_A_BR: 4...  
2246  PFOS_A: 79.6 ng/L <br>  PFOS_A_L + PFOS_A_BR: ...  
2247  PFOS_A: 2.63 ng/L <br> PFOS_A_L + PFOS_A_BR: 2...  
2248  PFPEA_A: 3.46 ng/L <br> PFHXA_A: 3.16 ng/L <br...  

[2249 rows x 8 columns]

In [14]:
facilities.set_crs(epsg=4326, inplace=True, allow_override=True)

facility  \
0     http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
1     http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
2     http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
3     http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
4     http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
...                                                 ...   
1279  http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
1280  http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
1281  http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
1282  http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   
1283  http://w3id.org/fio/v1/epa-frs-data#d.FRS-Faci...   

                          facWKT  \
0     POINT (-70.26075 44.06753)   
1     POINT (-70.35964 43.64599)   
2     POINT (-69.84726 44.71256)   
3     POINT (-70.18693 44.04928)   
4     POINT (-68.82583 44.73833)   
...                          ...   
1279   POINT (-84.4767 39.45796)   
1280  POINT (-82.96517 39.35644)   
1281  POINT (-80.97715 40.25527)   
1282  POINT (-84.05374 39.81373)   
1283  POINT (-83.78647 41.59144)   

                                           facilityName  \
0                MID MAINE WASTE - TO - ENERGY FACILITY   
1                                     ECOMAINE LANDFILL   
2     WASTE MANAGEMENT DISPOSALSERVICES OF MAINE, IN...   
3             LEWISTON SOLID WASTE & RECYCLING FACILITY   
4                    PENOBSCOT ENERGY RECOVERY FACILITY   
...                                                 ...   
1279                88TH REGIONAL SUPPORT COMMAND USARC   
1280        US ARMY NATIONAL GUARD RANGE - CAMP SHERMAN   
1281  88TH REGIONAL SUPPORT COMMAND SSG GEORGE J CON...   
1282             U.S. AIR FORCE WRIGHT-PATTERSON AFB OH   
1283         180TH FIGHTER WING/OHIO AIR NATIONAL GUARD   

                                       industry           industryName  
0     http://w3id.org/fio/v1/naics#NAICS-562212  Solid Waste Landfill   
1     http://w3id.org/fio/v1/naics#NAICS-562212  Solid Waste Landfill   
2     http://w3id.org/fio/v1/naics#NAICS-562212  Solid Waste Landfill   
3     http://w3id.org/fio/v1/naics#NAICS-562212  Solid Waste Landfill   
4     http://w3id.org/fio/v1/naics#NAICS-562212  Solid Waste Landfill   
...                                         ...                    ...  
1279  http://w3id.org/fio/v1/naics#NAICS-928110     National Security   
1280  http://w3id.org/fio/v1/naics#NAICS-928110     National Security   
1281  http://w3id.org/fio/v1/naics#NAICS-928110     National Security   
1282  http://w3id.org/fio/v1/naics#NAICS-928110     National Security   
1283  http://w3id.org/fio/v1/naics#NAICS-928110     National Security   

[1284 rows x 5 columns]

## Map

In [15]:
from branca.element import Figure

In [16]:
map = samplepoints.explore(name=f'<span style="color:DarkOrange;">Samples</span>', color='DarkOrange',
                           style_kwds=dict(style_function=lambda x: {"radius": float(x['properties']["Max"])if float(x['properties']["Max"]) < 10 else 12,
                                                                     "opacity":0.3,
                                                                     "color":'DimGray',
                                                                     }),
                           marker_kwds=dict(radius=6),
                           marker_type='circle_marker',
                           popup = ["samples", "Max", "unit", "results"],
                                ) #
#map

In [17]:
c = 0
colors = ['SaddleBrown', 'MidnightBlue']
for industry in list(facilities.industryName.unique()):
  #print(industry)
  #print(facilities[facilities['industryName']== industry].info())
  facilities[facilities['industryName']== industry].explore(m=map,
                                                            name=f'<span style="color:{colors[c]};">{industry}</span>',
                                                            color=colors[c],
                                                            marker_kwds=dict(radius=3),
                                                            popup=True)
  c += 1

In [18]:
folium.LayerControl(collapsed=False).add_to(map)
fig = Figure(width='100%', height=900)
fig.add_child(map)


In [19]:
fig.save('UIq1.html')

# Q2 - Filter to penobscot or Knox County

## questions

In [20]:
%%time

q1='''
PREFIX dcterms: <http://purl.org/dc/terms/>
PREFIX qudt: <http://qudt.org/schema/qudt/>
PREFIX skos: <http://www.w3.org/2004/02/skos/core#>
PREFIX geo: <http://www.opengis.net/ont/geosparql#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX naics: <http://w3id.org/fio/v1/naics#>
PREFIX spatial: <http://purl.org/spatialai/spatial/spatial-full#>
PREFIX kwgr: <http://stko-kwg.geog.ucsb.edu/lod/resource/>
PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX coso: <http://w3id.org/coso/v1/contaminoso#>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX fio: <http://w3id.org/fio/v1/fio#>

PREFIX owl: <http://www.w3.org/2002/07/owl#>
select DISTINCT ?samplePoint ?spWKT ?sample (GROUP_CONCAT(DISTINCT ?sampleId; separator="; ") as ?samples) (COUNT(DISTINCT ?subVal) as ?resultCount) (MAX(?result) as ?Max) ?unit (GROUP_CONCAT(DISTINCT ?subVal; separator=" <br> ") as ?results)
where {
        SERVICE <repository:FIO>{
        #find facilities
        ?s2neighbor kwg-ont:sfContains ?facility.
        ?facility fio:ofIndustry ?industry;
        		#geo:hasGeometry/geo:asWKT ?facWKT;
        		#rdfs:label ?facilityName.
        #?industry rdfs:label ?industryName.
        VALUES ?industry {naics:NAICS-562212 naics:NAICS-928110}.
    }
            SERVICE <repository:Spatial>{
        #determine near distance
        ?s2 kwg-ont:sfTouches|owl:sameAs ?s2neighbor.
        ?s2neighbor rdf:type kwg-ont:S2Cell_Level13.
        ?countySub rdf:type kwg-ont:AdministrativeRegion_3;
            kwg-ont:administrativePartOf ?county.
        VALUES ?county {kwgr:administrativeRegion.USA.23013 kwgr:administrativeRegion.USA.23019}
    }

    #find samples
    ?samplePoint kwg-ont:sfWithin ?s2;
      kwg-ont:sfWithin ?countySub;  #add countysub filter
    	rdf:type coso:SamplePoint;
    	geo:hasGeometry/geo:asWKT ?spWKT.
    ?s2 rdf:type kwg-ont:S2Cell_Level13.
    ?sample coso:fromSamplePoint ?samplePoint;
    	dcterms:identifier ?sampleId;
    	coso:sampleOfMaterialType/rdfs:label ?type.
    ?observation rdf:type coso:ContaminantObservation;
    	coso:observedAtSamplePoint ?samplePoint;
    	coso:ofSubstance/ skos:altLabel ?substance;
    	coso:hasResult/coso:measurementValue ?result;
    	coso:hasResult/coso:measurementUnit/qudt:symbol ?unit.
    BIND((CONCAT(?substance, ": ", str(?result) , " ", ?unit) ) as ?subVal)

    } GROUP BY ?samplePoint ?spWKT ?sample ?unit
'''
#What SAMPLES are NEAR to LANDFILLS or DOD facilities?
q2 = '''
PREFIX geo: <http://www.opengis.net/ont/geosparql#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX naics: <http://w3id.org/fio/v1/naics#>
PREFIX spatial: <http://purl.org/spatialai/spatial/spatial-full#>
PREFIX kwgr: <http://stko-kwg.geog.ucsb.edu/lod/resource/>
PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX coso: <http://w3id.org/coso/v1/contaminoso#>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX fio: <http://w3id.org/fio/v1/fio#>

#Where are landfills or dod facilities

select DISTINCT ?facility ?facWKT ?facilityName ?industry ?industryName where {
    #SERVICE <repository:Spatial>{
    #    #determine near distance
    #    ?s2 kwg-ont:sfTouches|owl:sameAs ?s2neighbor.
    #    ?s2neighbor rdf:type kwg-ont:S2Cell_Level13.
    #}
    SERVICE <repository:FIO>{
        #find facilities
        #?s2neighbor kwg-ont:sfContains ?facility.
        ?facility fio:ofIndustry ?industry;
        		geo:hasGeometry/geo:asWKT ?facWKT;
        		rdfs:label ?facilityName.
        ?industry rdfs:label ?industryName.
        VALUES ?industry {naics:NAICS-562212 naics:NAICS-928110}.
    }

}
'''
#County boundaries
q3 = '''
PREFIX geo: <http://www.opengis.net/ont/geosparql#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX naics: <http://w3id.org/fio/v1/naics#>
PREFIX spatial: <http://purl.org/spatialai/spatial/spatial-full#>
PREFIX kwgr: <http://stko-kwg.geog.ucsb.edu/lod/resource/>
PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX coso: <http://w3id.org/coso/v1/contaminoso#>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX fio: <http://w3id.org/fio/v1/fio#>
SELECT * WHERE {
SERVICE <repository:Spatial>{
        #?countySub rdf:type kwg-ont:AdministrativeRegion_3;
        #    kwg-ont:administrativePartOf ?county.
        VALUES ?county {kwgr:administrativeRegion.USA.23009 kwgr:administrativeRegion.USA.23019}
        ?county geo:hasGeometry/geo:asWKT ?countyWKT;
        rdfs:label ?countyName.
    }
    }
'''

CPU times: user 4 µs, sys: 0 ns, total: 4 µs
Wall time: 8.11 µs


In [21]:
def get_data(q1):
  sparqlGET.setQuery(q1)
  result = sparqlGET.query()
  df = convertToDataframe(result)
  return df


## query

In [22]:
%%time
samplepoints_KxPn = get_data(q1)

CPU times: user 22.8 ms, sys: 1.97 ms, total: 24.8 ms
Wall time: 7.15 s


In [23]:
#truncate results
samplepoints_KxPn['results'] = samplepoints_KxPn['results'].apply(lambda x: "<br> ".join(x.split('<br>')[0:20])+"<br> ... " if len(x.split('<br>')) > 16 else x)

In [24]:
samplepoints_KxPn

samplePoint  \
0    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
1    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
3    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
4    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
..                                                 ...   
109  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
110  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
111  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
112  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
113  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   

                              spWKT  \
0    POINT (-68.8624856 44.7694029)   
1    POINT (-68.8624856 44.7694029)   
2    POINT (-68.8624856 44.7694029)   
3    POINT (-68.8624856 44.7694029)   
4    POINT (-68.8624856 44.7694029)   
..                              ...   
109  POINT (-68.8332705 44.8058271)   
110  POINT (-68.8353908 44.8056591)   
111  POINT (-68.8063563 44.8260024)   
112  POINT (-68.8063563 44.8260024)   
113  POINT (-68.8063563 44.8260024)   

                                                sample  \
0    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
1    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
3    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
4    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
..                                                 ...   
109  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
110  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
111  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
112  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
113  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   

                         samples  resultCount      Max  unit  \
0                      LTXXXXBE9          123   2710.0  ng/L   
1                      LTLEAXBGG          123   2710.0  ng/L   
2                      LTLEAXBJ6          123   2710.0  ng/L   
3                      LTLEAXCC3          123   2710.0  ng/L   
4                    LTLEAXCC3RE          123   2710.0  ng/L   
..                           ...          ...      ...   ...   
109                         MW-4           39  53040.8  ng/L   
110                     DOW-MW-4           17   32.938  ng/L   
111   KRB-LMB-C1(1,2,3,4,5)-2023           21     9.51  ng/g   
112   KRB-SMB-C1(1,2,3,4,5)-2023           21     9.51  ng/g   
113  KRB-SMB-C2(6,7,8,9,10)-2023           21     9.51  ng/g   

                                               results  
0    PFUNDA_A: 11.6 ng/L <br>  N-MeFOSAA_A: 51.5 ng...  
1    PFUNDA_A: 11.6 ng/L <br>  N-MeFOSAA_A: 51.5 ng...  
2    PFUNDA_A: 11.6 ng/L <br>  N-MeFOSAA_A: 51.5 ng...  
3    PFUNDA_A: 11.6 ng/L <br>  N-MeFOSAA_A: 51.5 ng...  
4    PFUNDA_A: 11.6 ng/L <br>  N-MeFOSAA_A: 51.5 ng...  
..                                                 ...  
109  PFOS_A: 6460.0 ng/L <br>  PFOS_A_L + PFOS_A_BR...  
110  PFOS_A: 4.77 ng/L <br>  PFOS_A_L + PFOS_A_BR: ...  
111  PFDOA: 0.2091 ng/g <br>  PFUNDA: 0.5059 ng/g <...  
112  PFDOA: 0.2091 ng/g <br>  PFUNDA: 0.5059 ng/g <...  
113  PFDOA: 0.2091 ng/g <br>  PFUNDA: 0.5059 ng/g <...  

[114 rows x 8 columns]

In [25]:
samplepoints_KxPn['spWKT'] = samplepoints_KxPn['spWKT'].apply(wkt.loads)
samplepoints_KxPn = gpd.GeoDataFrame(samplepoints_KxPn, geometry='spWKT')
samplepoints_KxPn.set_crs(epsg=4326, inplace=True, allow_override=True)

samplePoint  \
0    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
1    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
3    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
4    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
..                                                 ...   
109  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
110  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
111  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
112  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
113  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   

                          spWKT  \
0     POINT (-68.86249 44.7694)   
1     POINT (-68.86249 44.7694)   
2     POINT (-68.86249 44.7694)   
3     POINT (-68.86249 44.7694)   
4     POINT (-68.86249 44.7694)   
..                          ...   
109  POINT (-68.83327 44.80583)   
110  POINT (-68.83539 44.80566)   
111    POINT (-68.80636 44.826)   
112    POINT (-68.80636 44.826)   
113    POINT (-68.80636 44.826)   

                                                sample  \
0    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
1    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
2    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
3    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
4    http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
..                                                 ...   
109  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
110  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
111  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
112  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   
113  http://w3id.org/sawgraph/v1/me-egad-data#sampl...   

                         samples  resultCount      Max  unit  \
0                      LTXXXXBE9          123   2710.0  ng/L   
1                      LTLEAXBGG          123   2710.0  ng/L   
2                      LTLEAXBJ6          123   2710.0  ng/L   
3                      LTLEAXCC3          123   2710.0  ng/L   
4                    LTLEAXCC3RE          123   2710.0  ng/L   
..                           ...          ...      ...   ...   
109                         MW-4           39  53040.8  ng/L   
110                     DOW-MW-4           17   32.938  ng/L   
111   KRB-LMB-C1(1,2,3,4,5)-2023           21     9.51  ng/g   
112   KRB-SMB-C1(1,2,3,4,5)-2023           21     9.51  ng/g   
113  KRB-SMB-C2(6,7,8,9,10)-2023           21     9.51  ng/g   

                                               results  
0    PFUNDA_A: 11.6 ng/L <br>  N-MeFOSAA_A: 51.5 ng...  
1    PFUNDA_A: 11.6 ng/L <br>  N-MeFOSAA_A: 51.5 ng...  
2    PFUNDA_A: 11.6 ng/L <br>  N-MeFOSAA_A: 51.5 ng...  
3    PFUNDA_A: 11.6 ng/L <br>  N-MeFOSAA_A: 51.5 ng...  
4    PFUNDA_A: 11.6 ng/L <br>  N-MeFOSAA_A: 51.5 ng...  
..                                                 ...  
109  PFOS_A: 6460.0 ng/L <br>  PFOS_A_L + PFOS_A_BR...  
110  PFOS_A: 4.77 ng/L <br>  PFOS_A_L + PFOS_A_BR: ...  
111  PFDOA: 0.2091 ng/g <br>  PFUNDA: 0.5059 ng/g <...  
112  PFDOA: 0.2091 ng/g <br>  PFUNDA: 0.5059 ng/g <...  
113  PFDOA: 0.2091 ng/g <br>  PFUNDA: 0.5059 ng/g <...  

[114 rows x 8 columns]

In [26]:
counties = get_data(q3)

In [27]:
counties

county  \
0  http://stko-kwg.geog.ucsb.edu/lod/resource/adm...   
1  http://stko-kwg.geog.ucsb.edu/lod/resource/adm...   

                                           countyWKT               countyName  
0  POLYGON ((-68.16994 44.186122, -68.169916 44.1...    Hancock County, Maine  
1  POLYGON ((-68.409296 45.573578, -68.406286 45....  Penobscot County, Maine

In [28]:
counties['countyWKT'] = counties['countyWKT'].apply(wkt.loads)
counties = gpd.GeoDataFrame(counties, geometry='countyWKT')
counties.set_crs(epsg=4326, inplace=True, allow_override=True)

county  \
0  http://stko-kwg.geog.ucsb.edu/lod/resource/adm...   
1  http://stko-kwg.geog.ucsb.edu/lod/resource/adm...   

                                           countyWKT               countyName  
0  POLYGON ((-68.16994 44.18612, -68.16992 44.186...    Hancock County, Maine  
1  POLYGON ((-68.4093 45.57358, -68.40629 45.5740...  Penobscot County, Maine

## Map

In [29]:
map2 = counties.explore(name='Counties', style_kwds=dict(color='Gray', fill=0.0))

In [30]:
samplepoints_KxPn.explore(m=map2, name=f'<span style="color:DarkOrange;">Samples</span>', color='DarkOrange',
                           style_kwds=dict(style_function=lambda x: {"radius": float(x['properties']["Max"])if float(x['properties']["Max"]) < 10 else 12,
                                                                     "opacity":0.3,
                                                                     "color":'DimGray',
                                                                     }),
                           marker_kwds=dict(radius=6),
                           marker_type='circle_marker',
                           popup = ["samples", "Max", "unit", "results"],
                                ) #
#map

In [31]:
c = 0
colors = ['SaddleBrown', 'MidnightBlue']
for industry in list(facilities.industryName.unique()):
  #print(industry)
  #print(facilities[facilities['industryName']== industry].info())
  facilities[facilities['industryName']== industry].explore(m=map2,
                                                            name=f'<span style="color:{colors[c]};">{industry}</span>',
                                                            color=colors[c],
                                                            marker_kwds=dict(radius=3),
                                                            popup=True,
                                                            hidden=True)
  c += 1

In [32]:
folium.LayerControl(collapsed=False).add_to(map2)
fig2 = Figure(width='100%', height=900)
fig2.add_child(map2)

In [33]:
fig2.save('UIq2.html')

# Q3 - What surface water in Knox/Penobsocot is near landfill or defense?

## query


In [34]:
q1='''
PREFIX dcterms: <http://purl.org/dc/terms/>
PREFIX geo: <http://www.opengis.net/ont/geosparql#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX naics: <http://w3id.org/fio/v1/naics#>
PREFIX spatial: <http://purl.org/spatialai/spatial/spatial-full#>
PREFIX kwgr: <http://stko-kwg.geog.ucsb.edu/lod/resource/>
PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX coso: <http://w3id.org/coso/v1/contaminoso#>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX fio: <http://w3id.org/fio/v1/fio#>
PREFIX owl: <http://www.w3.org/2002/07/owl#>
PREFIX hyf: <https://www.opengis.net/def/schema/hy_features/hyf/>
PREFIX nhdplusv2: <http://nhdplusv2.spatialai.org/v1/nhdplusv2#>
PREFIX hyfo: <http://hyfo.spatialai.org/v1/hyfo#>

select DISTINCT ?surfacewater ?surfacewatername ?waterType ?swWKT ?reachCode ?COMID
where {
        SERVICE <repository:FIO>{
        #find facilities
        ?s2neighbor kwg-ont:sfContains ?facility.
        ?facility fio:ofIndustry ?industry;
        		#geo:hasGeometry/geo:asWKT ?facWKT;
        		#rdfs:label ?facilityName.
        #?industry rdfs:label ?industryName.
        VALUES ?industry {naics:NAICS-562212 naics:NAICS-928110}.
    }

        SERVICE <repository:Spatial>{
        #determine near distance
        ?s2 kwg-ont:sfTouches|owl:sameAs ?s2neighbor.
        ?s2neighbor rdf:type kwg-ont:S2Cell_Level13;
        	spatial:connectedTo ?countySub.  #since hydrology is not aligned to admin region, we filter s2 neighborhood by admin region
        ?countySub rdf:type kwg-ont:AdministrativeRegion_3;
            kwg-ont:administrativePartOf ?county.
        VALUES ?county {kwgr:administrativeRegion.USA.23013 kwgr:administrativeRegion.USA.23019}
        }

   		#find surface water
    	SERVICE <repository:Hydrology>{
    	?surfacewater rdf:type ?watertype;
        	spatial:connectedTo ?s2neighbor;
        	#spatial:connectedTo ?countySub;
        	geo:hasGeometry/ geo:asWKT ?swWKT.
        OPTIONAL {?surfacewater rdfs:label ?surfacewatername;
        	nhdplusv2:hasFTYPE ?waterType;
            nhdplusv2:hasCOMID ?COMID;
			nhdplusv2:hasReachCode ?reachCode.}
      VALUES ?watertype {hyf:HY_HydroFeature hyfo:WaterFeatureRepresentation}
	}
}
'''

In [35]:
%%time
sparqlGET.setQuery(q1)
surfacewater_result = sparqlGET.query()
surfacewater = convertToDataframe(surfacewater_result)

CPU times: user 10.4 ms, sys: 1.2 ms, total: 11.6 ms
Wall time: 1.61 s


In [36]:
surfacewater

surfacewater     surfacewatername  \
0   https://geoconnex.us/nhdplusv2/comid/1736934      Penobscot River   
1   https://geoconnex.us/nhdplusv2/comid/1743088  Souadabscook Stream   
2   https://geoconnex.us/nhdplusv2/comid/1736956      Penobscot River   
3   https://geoconnex.us/nhdplusv2/comid/1735920                  NaN   
4   https://geoconnex.us/nhdplusv2/comid/1735580                  NaN   
5   https://geoconnex.us/nhdplusv2/comid/2680590          Caribou Bog   
6   https://geoconnex.us/nhdplusv2/comid/1735128                  NaN   
7   https://geoconnex.us/nhdplusv2/comid/1735126                  NaN   
8   https://geoconnex.us/nhdplusv2/comid/1735764                  NaN   
9   https://geoconnex.us/nhdplusv2/comid/1736822                  NaN   
10  https://geoconnex.us/nhdplusv2/comid/1735770                  NaN   
11  https://geoconnex.us/nhdplusv2/comid/1736826                  NaN   
12  https://geoconnex.us/nhdplusv2/comid/1736816                  NaN   
13  https://geoconnex.us/nhdplusv2/comid/1713202       Hathaway Brook   

         waterType                                              swWKT  \
0   ArtificialPath  LINESTRING (-68.80168867031273 44.761442397187...   
1   ArtificialPath  LINESTRING (-68.82933060360313 44.745144730546...   
2   ArtificialPath  LINESTRING (-68.82832987027138 44.743936997215...   
3              NaN  LINESTRING (-68.87467600353273 44.775925530498...   
4              NaN  LINESTRING (-68.71628887044528 44.979869596848...   
5       SwampMarsh  POLYGON ((-68.74949507039372 44.93079373025847...   
6              NaN  POLYGON ((-68.671582203848 44.86993919701956, ...   
7              NaN  POLYGON ((-68.67433040384373 44.87477013034544...   
8              NaN  LINESTRING (-68.66801840385352 44.877348930341...   
9              NaN  LINESTRING (-68.67120227051527 44.877439197007...   
10             NaN  LINESTRING (-68.67448007051013 44.874716797012...   
11             NaN  LINESTRING (-68.67460787050993 44.873687797013...   
12             NaN  LINESTRING (-68.66791907052033 44.877264197008...   
13     StreamRiver  LINESTRING (-68.57707560399467 45.655312595800...   

         reachCode    COMID  
0   01020005000036  1736934  
1   01020005000408  1743088  
2   01020005000034  1736956  
3              NaN      NaN  
4              NaN      NaN  
5             None  2680590  
6              NaN      NaN  
7              NaN      NaN  
8              NaN      NaN  
9              NaN      NaN  
10             NaN      NaN  
11             NaN      NaN  
12             NaN      NaN  
13  01020002000255  1713202

In [37]:
surfacewater['swWKT'] = surfacewater['swWKT'].apply(wkt.loads)
surfacewater = gpd.GeoDataFrame(surfacewater, geometry='swWKT')

In [38]:
surfacewater.set_crs(epsg=4326, inplace=True, allow_override=True)

surfacewater     surfacewatername  \
0   https://geoconnex.us/nhdplusv2/comid/1736934      Penobscot River   
1   https://geoconnex.us/nhdplusv2/comid/1743088  Souadabscook Stream   
2   https://geoconnex.us/nhdplusv2/comid/1736956      Penobscot River   
3   https://geoconnex.us/nhdplusv2/comid/1735920                  NaN   
4   https://geoconnex.us/nhdplusv2/comid/1735580                  NaN   
5   https://geoconnex.us/nhdplusv2/comid/2680590          Caribou Bog   
6   https://geoconnex.us/nhdplusv2/comid/1735128                  NaN   
7   https://geoconnex.us/nhdplusv2/comid/1735126                  NaN   
8   https://geoconnex.us/nhdplusv2/comid/1735764                  NaN   
9   https://geoconnex.us/nhdplusv2/comid/1736822                  NaN   
10  https://geoconnex.us/nhdplusv2/comid/1735770                  NaN   
11  https://geoconnex.us/nhdplusv2/comid/1736826                  NaN   
12  https://geoconnex.us/nhdplusv2/comid/1736816                  NaN   
13  https://geoconnex.us/nhdplusv2/comid/1713202       Hathaway Brook   

         waterType                                              swWKT  \
0   ArtificialPath  LINESTRING (-68.80169 44.76144, -68.80257 44.7...   
1   ArtificialPath  LINESTRING (-68.82933 44.74514, -68.82931 44.7...   
2   ArtificialPath  LINESTRING (-68.82833 44.74394, -68.82883 44.7...   
3              NaN  LINESTRING (-68.87468 44.77593, -68.87448 44.7...   
4              NaN  LINESTRING (-68.71629 44.97987, -68.71629 44.9...   
5       SwampMarsh  POLYGON ((-68.7495 44.93079, -68.74908 44.9310...   
6              NaN  POLYGON ((-68.67158 44.86994, -68.67203 44.869...   
7              NaN  POLYGON ((-68.67433 44.87477, -68.67448 44.874...   
8              NaN  LINESTRING (-68.66802 44.87735, -68.66873 44.8...   
9              NaN  LINESTRING (-68.6712 44.87744, -68.67128 44.87...   
10             NaN  LINESTRING (-68.67448 44.87472, -68.67461 44.8...   
11             NaN  LINESTRING (-68.67461 44.87369, -68.67456 44.8...   
12             NaN  LINESTRING (-68.66792 44.87726, -68.66794 44.8...   
13     StreamRiver  LINESTRING (-68.57708 45.65531, -68.57629 45.6...   

         reachCode    COMID  
0   01020005000036  1736934  
1   01020005000408  1743088  
2   01020005000034  1736956  
3              NaN      NaN  
4              NaN      NaN  
5             None  2680590  
6              NaN      NaN  
7              NaN      NaN  
8              NaN      NaN  
9              NaN      NaN  
10             NaN      NaN  
11             NaN      NaN  
12             NaN      NaN  
13  01020002000255  1713202

## Map

In [39]:
map3 = counties.explore(name='Counties', style_kwds=dict(color='Gray', fill=0.0))

In [40]:
surfacewater.explore(m=map3, name=f'<span style="color:Blue;">Surface Water</span>', color='Blue',
                           style_kwds=dict(color='Blue', fill=0.8),

                           #popup = ["samples", "Max", "unit", "results"],
                                ) #

In [41]:
c = 0
for industry in list(facilities.industryName.unique()):
  #print(industry)
  #print(facilities[facilities['industryName']== industry].info())
  facilities[facilities['industryName']== industry].explore(m=map3,
                                                            name=f'<span style="color:{colors[c]};">{industry}</span>',
                                                            color=colors[c],
                                                            marker_kwds=dict(radius=3),
                                                            popup=True,
                                                            hidden=True)
  c += 1

In [42]:
folium.LayerControl(collapsed=False).add_to(map3)
fig3 = Figure(width='100%', height=900)
fig3.add_child(map3)

In [43]:
fig3.save('UIq3.html')

# Q4 - What surface water is downstream of landfill or dod sites?

## Query

In [44]:
q1='''
PREFIX dcterms: <http://purl.org/dc/terms/>
PREFIX geo: <http://www.opengis.net/ont/geosparql#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX naics: <http://w3id.org/fio/v1/naics#>
PREFIX spatial: <http://purl.org/spatialai/spatial/spatial-full#>
PREFIX kwgr: <http://stko-kwg.geog.ucsb.edu/lod/resource/>
PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX coso: <http://w3id.org/coso/v1/contaminoso#>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX fio: <http://w3id.org/fio/v1/fio#>
PREFIX owl: <http://www.w3.org/2002/07/owl#>
PREFIX hyf: <https://www.opengis.net/def/schema/hy_features/hyf/>
PREFIX nhdplusv2: <http://nhdplusv2.spatialai.org/v1/nhdplusv2#>

PREFIX hyfo: <http://hyfo.spatialai.org/v1/hyfo#>
select DISTINCT ?surfacewater ?surfacewatername ?waterType ?swWKT ?reachCode ?COMID
where {
        SERVICE <repository:FIO>{
        #find facilities
        ?s2neighbor kwg-ont:sfContains ?facility.
        ?facility fio:ofIndustry ?industry;
        		#geo:hasGeometry/geo:asWKT ?facWKT;
        		#rdfs:label ?facilityName.
        #?industry rdfs:label ?industryName.
        VALUES ?industry {naics:NAICS-562212 naics:NAICS-928110}.
    }

        SERVICE <repository:Spatial>{
        #determine near distance
        ?s2 kwg-ont:sfTouches|owl:sameAs ?s2neighbor.
        ?s2neighbor rdf:type kwg-ont:S2Cell_Level13;
        	spatial:connectedTo ?countySub.  #since hydrology is not aligned to admin region, we filter s2 neighborhood by admin region
        #?s2downstream rdf:type kwg-ont:S2Cell_Level13;  # to filter to only water in the county
        #	spatial:connectedTo ?countySub.
        ?countySub rdf:type kwg-ont:AdministrativeRegion_3;
            kwg-ont:administrativePartOf ?county.
        VALUES ?county {kwgr:administrativeRegion.USA.23013 kwgr:administrativeRegion.USA.23019}
        }

   		#find surface water
    	SERVICE <repository:Hydrology>{
    	?stream rdf:type hyfo:WaterFeatureRepresentation;  #hyf:HY_HydroFeature
        	spatial:connectedTo ?s2neighbor;
        		hyf:downstreamWaterBody+ ?surfacewater.
        	#spatial:connectedTo ?countySub;
        ?surfacewater geo:hasGeometry/ geo:asWKT ?swWKT.
              # spatial:connectedTo ?s2downstream.
        OPTIONAL {?surfacewater rdfs:label ?surfacewatername;
        	nhdplusv2:hasFTYPE ?waterType;
            nhdplusv2:hasCOMID ?COMID;
			nhdplusv2:hasReachCode ?reachCode.}

	}
}
'''

In [45]:
%%time
sparqlGET.setQuery(q1)
surfacewater_result2 = sparqlGET.query()
surfacewater2 = convertToDataframe(surfacewater_result2)

CPU times: user 21.9 ms, sys: 1.51 ms, total: 23.4 ms
Wall time: 1.56 s


In [46]:
surfacewater2

surfacewater surfacewatername  \
0    https://geoconnex.us/nhdplusv2/comid/1736934  Penobscot River   
1    https://geoconnex.us/nhdplusv2/comid/1736956  Penobscot River   
2    https://geoconnex.us/nhdplusv2/comid/1736986  Penobscot River   
3    https://geoconnex.us/nhdplusv2/comid/1736996  Penobscot River   
4    https://geoconnex.us/nhdplusv2/comid/1737000  Penobscot River   
..                                            ...              ...   
205  https://geoconnex.us/nhdplusv2/comid/1736690  Penobscot River   
206  https://geoconnex.us/nhdplusv2/comid/1736696  Penobscot River   
207  https://geoconnex.us/nhdplusv2/comid/1736756  Penobscot River   
208  https://geoconnex.us/nhdplusv2/comid/1743070              NaN   
209  https://geoconnex.us/nhdplusv2/comid/1736698              NaN   

          waterType                                              swWKT  \
0    ArtificialPath  LINESTRING (-68.80168867031273 44.761442397187...   
1    ArtificialPath  LINESTRING (-68.82832987027138 44.743936997215...   
2    ArtificialPath  LINESTRING (-68.83221600359866 44.735442997228...   
3    ArtificialPath  LINESTRING (-68.83834840358912 44.693870797292...   
4    ArtificialPath  LINESTRING (-68.83376300359623 44.690685930631...   
..              ...                                                ...   
205  ArtificialPath  LINESTRING (-68.63940760389795 44.984916596841...   
206  ArtificialPath  LINESTRING (-68.63871267056567 44.982146796845...   
207  ArtificialPath  LINESTRING (-68.64426233722372 44.965335330204...   
208             NaN  LINESTRING (-68.64426233722372 44.965335330204...   
209             NaN  LINESTRING (-68.64530620388877 44.966143596870...   

          reachCode    COMID  
0    01020005000036  1736934  
1    01020005000034  1736956  
2    01020005000034  1736986  
3    01020005000033  1736996  
4    01020005000033  1737000  
..              ...      ...  
205  01020005001705  1736690  
206  01020005001729  1736696  
207  01020005000073  1736756  
208             NaN      NaN  
209             NaN      NaN  

[210 rows x 6 columns]

#

In [47]:
surfacewater2['swWKT'] = surfacewater2['swWKT'].apply(wkt.loads)
surfacewater2 = gpd.GeoDataFrame(surfacewater2, geometry='swWKT')

In [48]:
surfacewater.set_crs(epsg=4326, inplace=True, allow_override=True)

surfacewater     surfacewatername  \
0   https://geoconnex.us/nhdplusv2/comid/1736934      Penobscot River   
1   https://geoconnex.us/nhdplusv2/comid/1743088  Souadabscook Stream   
2   https://geoconnex.us/nhdplusv2/comid/1736956      Penobscot River   
3   https://geoconnex.us/nhdplusv2/comid/1735920                  NaN   
4   https://geoconnex.us/nhdplusv2/comid/1735580                  NaN   
5   https://geoconnex.us/nhdplusv2/comid/2680590          Caribou Bog   
6   https://geoconnex.us/nhdplusv2/comid/1735128                  NaN   
7   https://geoconnex.us/nhdplusv2/comid/1735126                  NaN   
8   https://geoconnex.us/nhdplusv2/comid/1735764                  NaN   
9   https://geoconnex.us/nhdplusv2/comid/1736822                  NaN   
10  https://geoconnex.us/nhdplusv2/comid/1735770                  NaN   
11  https://geoconnex.us/nhdplusv2/comid/1736826                  NaN   
12  https://geoconnex.us/nhdplusv2/comid/1736816                  NaN   
13  https://geoconnex.us/nhdplusv2/comid/1713202       Hathaway Brook   

         waterType                                              swWKT  \
0   ArtificialPath  LINESTRING (-68.80169 44.76144, -68.80257 44.7...   
1   ArtificialPath  LINESTRING (-68.82933 44.74514, -68.82931 44.7...   
2   ArtificialPath  LINESTRING (-68.82833 44.74394, -68.82883 44.7...   
3              NaN  LINESTRING (-68.87468 44.77593, -68.87448 44.7...   
4              NaN  LINESTRING (-68.71629 44.97987, -68.71629 44.9...   
5       SwampMarsh  POLYGON ((-68.7495 44.93079, -68.74908 44.9310...   
6              NaN  POLYGON ((-68.67158 44.86994, -68.67203 44.869...   
7              NaN  POLYGON ((-68.67433 44.87477, -68.67448 44.874...   
8              NaN  LINESTRING (-68.66802 44.87735, -68.66873 44.8...   
9              NaN  LINESTRING (-68.6712 44.87744, -68.67128 44.87...   
10             NaN  LINESTRING (-68.67448 44.87472, -68.67461 44.8...   
11             NaN  LINESTRING (-68.67461 44.87369, -68.67456 44.8...   
12             NaN  LINESTRING (-68.66792 44.87726, -68.66794 44.8...   
13     StreamRiver  LINESTRING (-68.57708 45.65531, -68.57629 45.6...   

         reachCode    COMID  
0   01020005000036  1736934  
1   01020005000408  1743088  
2   01020005000034  1736956  
3              NaN      NaN  
4              NaN      NaN  
5             None  2680590  
6              NaN      NaN  
7              NaN      NaN  
8              NaN      NaN  
9              NaN      NaN  
10             NaN      NaN  
11             NaN      NaN  
12             NaN      NaN  
13  01020002000255  1713202

## map


In [49]:
map4 = counties.explore(name='Counties', style_kwds=dict(color='Gray', fill=0.0))

In [50]:
surfacewater2.explore(m=map4, name=f'<span style="color:Blue;">Surface Water</span>', color='Blue',
                           style_kwds=dict(color='Blue', fill=0.8),

                           #popup = ["samples", "Max", "unit", "results"],
                                ) #

In [51]:
c = 0
for industry in list(facilities.industryName.unique()):
  #print(industry)
  #print(facilities[facilities['industryName']== industry].info())
  facilities[facilities['industryName']== industry].explore(m=map4,
                                                            name=f'<span style="color:{colors[c]};">{industry}</span>',
                                                            color=colors[c],
                                                            marker_kwds=dict(radius=3),
                                                            popup=True,
                                                            hidden=True)
  c += 1

In [52]:
folium.LayerControl(collapsed=False).add_to(map4)
fig4 = Figure(width='100%', height=900)
fig4.add_child(map4)

In [53]:
fig4.save('UIq4.html')